In [1]:
!pip install -U sentence-transformers

     |████████████████████████████████| 85 kB 2.6 MB/s 
     |████████████████████████████████| 2.8 MB 37.7 MB/s 
     |████████████████████████████████| 1.2 MB 40.5 MB/s 
     |████████████████████████████████| 50 kB 6.7 MB/s 
     |████████████████████████████████| 895 kB 47.7 MB/s 
     |████████████████████████████████| 3.3 MB 30.9 MB/s 
     |████████████████████████████████| 636 kB 41.3 MB/s 
  Created wheel for sentence-transformers: filename=sentence_transformers-2.0.0-py3-none-any.whl size=126710 sha256=e4005d0fa76ed2122729bdef65b3c80ff23cebfc130b393433f498b88284296c
  Stored in directory: /root/.cache/pip/wheels/d1/c1/0f/faafd427f705c4b012274ba60d9a91d75830306811e1355293
Successfully built sentence-transformers
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13


# Embedding With Sentence BERT

In [2]:
import pandas as pd
import zipfile
from google.colab import drive

In [3]:
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import collections
import wordcloud
from sentence_transformers import SentenceTransformer
import tensorflow as tf
from sklearn.model_selection import GridSearchCV
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.manifold import TSNE
from sklearn.cluster import KMeans
import spacy
import gensim
import gensim.corpora as corpora
from gensim.models import LdaMulticore, CoherenceModel, Phrases, LdaModel
import os
import time
from tqdm import tqdm
import warnings
from collections import Counter
from nltk.tokenize import ToktokTokenizer
from bokeh.models import ColumnDataSource, HoverTool
from bokeh.plotting import figure, show, output_notebook
warnings.filterwarnings('ignore')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [4]:
drive.mount('/content/drive/', force_remount=True)
zip_ref = zipfile.ZipFile('/content/drive/MyDrive/ML/tokenized.zip', 'r')
zip_ref.extractall('/tmp')
zip_ref.close()

Mounted at /content/drive/


In [5]:
data = pd.read_csv('/tmp/tokenized.csv')
data.head()

title  ...                                      phrase-tokens
0  Surgical Performance Is Not Negatively Impacte...  ...  ['background', 'shortag_suppli', 'equip', 'ide...
1  Indications for Inpatient Magnetoencephalograp...  ...  ['method', 'local', 'zone', 'area', 'part', 'e...
2  Information about COVID-19 for deaf people: an...  ...  ['video', 'inform', 'sign', 'languag', 'studi'...
3  The Association Between Health Status and Inso...  ...  ['object', 'studi', 'mediat', 'role', 'fear', ...
4  Therapeutic targeting of interleukin-6 for the...  ...  ['diseas', 'infect', 'respiratori_syndrom', 'c...

[5 rows x 4 columns]

In [6]:
model = SentenceTransformer('stsb-distilroberta-base-v2',device='cuda')

Downloading:   0%|          | 0.00/1.09k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/3.71k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/680 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/122 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/456k [00:00<?, ?B/s]

...

Downloading:   0%|          | 0.00/239 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.12k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/798k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [8]:
sentences = []
for i in range(len(data)):
  sen = data['tokens'][i].replace("[",'').replace("]",'').replace("'",'').replace(',','')
  sentences.append(sen)

In [9]:
embedding = model.encode(sentences, convert_to_numpy = True, show_progress_bar=True)

Batches:   0%|          | 0/1582 [00:00<?, ?it/s]

## Clustering Using K-Means

In [10]:
num_clusters = 9
clustering_model = KMeans(n_clusters=num_clusters,
                          n_init=10,
                          max_iter=300,
                          tol=1e-4,  
                          random_state=98)
clustering_model.fit(embedding)
cluster_assignment = clustering_model.labels_

In [11]:
df_docs = pd.DataFrame(sentences,columns=['Doc'])
df_docs['Topic'] = cluster_assignment
df_docs['Doc_ID'] = range(len(df_docs))
docs_per_topic = df_docs.groupby(['Topic'],as_index=False).agg({'Doc':' '.join})
docs_per_topic

Topic                                                Doc
0      0  object studi mediat role fear associ health st...
1      1  method local zone area part evalu patient meg ...
2      2  respiratori syndrom viru worldwid effort drug ...
3      3  doubt pandem impact tourism reason travel rest...
4      4  individu hospit symptom spectrum manifest haul...
5      5  studi manag control organis respons video inte...
6      6  diseas infect respiratori syndrom china rate i...
7      7  studi valu assess bedsid ultrasound diagnosi l...
8      8  background shortag suppli equip idea mask solu...

## Gathering Important Words from Topics with c-TF-IDF

In [12]:
def c_tf_idf(documents, m, ngram_range=(1, 1)):
    count = CountVectorizer(ngram_range=ngram_range, stop_words="english").fit(documents)
    t = count.transform(documents).toarray()
    w = t.sum(axis=1)
    tf = np.divide(t.T, w)
    sum_t = t.sum(axis=0)
    idf = np.log(np.divide(m, sum_t)).reshape(-1, 1)
    tf_idf = np.multiply(tf, idf)

    return tf_idf, count
  
tf_idf, count = c_tf_idf(docs_per_topic.Doc.values, m=len(data))

In [13]:
def extract_top_n_words_per_topic(tf_idf, count, docs_per_topic, n=20):
    words = count.get_feature_names()
    labels = list(docs_per_topic.Topic)
    tf_idf_transposed = tf_idf.T
    indices = tf_idf_transposed.argsort()[:, -n:]
    top_n_words = {label: [(words[j], tf_idf_transposed[i][j]) for j in indices[i]][::-1] for i, label in enumerate(labels)}
    return top_n_words

def extract_topic_sizes(df):
    topic_sizes = (df.groupby(['Topic'])
                     .Doc
                     .count()
                     .reset_index()
                     .rename({"Topic": "Topic", "Doc": "Size"}, axis='columns')
                     .sort_values("Size", ascending=False))
    return topic_sizes

top_n_words = extract_top_n_words_per_topic(tf_idf, count, docs_per_topic, n=20)
topic_sizes = extract_topic_sizes(df_docs)
topic_sizes.head(10)

Topic  Size
2      2  7235
7      7  7187
0      0  6770
1      1  6564
3      3  6523
6      6  6031
8      8  5587
5      5  2571
4      4  2132

- From the dataframe above, it shows that each topic has its own frequencies on the documents. As we can see, topic 2, 7, 0, 1 on our cluster topics.

In [14]:
print(top_n_words[2][:10])
print(top_n_words[7][:10])
print(top_n_words[0][:10])
print(top_n_words[1][:10])

[('cell', 0.028853061877968208), ('protein', 0.027681994406387373), ('drug', 0.019553632853080035), ('antibodi', 0.01915015926797777), ('gene', 0.015529086517263665), ('express', 0.014684345959457213), ('receptor', 0.014404337630728436), ('vaccin', 0.014332362553430985), ('immun', 0.014142804914756031), ('host', 0.013000395242744855)]
[('mortal', 0.018829455849793883), ('hospit', 0.013980425520875871), ('admiss', 0.013087331373973821), ('outcom', 0.012997026282478286), ('symptom', 0.012149705331596608), ('age', 0.011912920786925582), ('respiratori', 0.011860466997819638), ('risk', 0.011822869519161441), ('ventil', 0.011156448907216968), ('sever', 0.010692430879724152)]
[('anxieti', 0.016097187033534417), ('health', 0.01569291446204029), ('children', 0.012997656947684523), ('worker', 0.012979502504795164), ('depress', 0.012884602049276963), ('women', 0.012800843572326977), ('particip', 0.012159755394907693), ('stress', 0.011013070169695487), ('survey', 0.010695537142130625), ('healthcar

## Topic Visualization with Word Cloud

In [15]:
fig = plt.figure(figsize=(16,20))
for label,word_prob_pairs in top_n_words.items():
    top_15_words_prob_pairs = dict(word_prob_pairs[:15])
    ax= fig.add_subplot(5,2,label+1)
    wcloud = wordcloud.WordCloud(background_color='white')
    wcloud.generate_from_frequencies(top_15_words_prob_pairs)
    ax.imshow(wcloud)
    for pos in ['left','right','top','bottom']:
        ax.spines[pos].set_color(None)
    ax.set_xticks([])
    ax.set_yticks([])
    ax.set_title(f'Topic {label+1}' ,fontsize=14)

- Topic 1 probably talk about **Mental Health During Pandemic**, since it has word such as "anxieti","health","depress"
- Topic 2 probably talk about **Treatment Methods**, since it has word such as "treatment", "care",  "surgeri"
- Topic 3 probably talk about **Drug Treatment Effect**, since it has word such as 'drug', 'immun', 'protein', 'antibodi'
- Topic 4 probably talk about **Pandemic Impact On Daily Life**, since it has word such as "impact","food","media"
- Topic 5 probably talk about **Respiratory Condition On Infected Patient**, since it has word such as 'pneumonia', 'lung', 'syndrom'
- Topic 6 probably talk about **School Activity During Pandemic**, since it has word such as 'onlin', 'educ', 'student', 'school'
- Topic 7 probably talk about **Transmission Dynamic Of Virus**, since it has word such as "pandem", "outbreak", "spread"
- Topic 8 probably talk about **Mortality**, since it has word such as "mortal", "age", "death"
- Topic 9 probably talk about **Analysis and Technology**, since it has word such as "model", "network, "algorithm"




## AutoEncoding

In [16]:
ENCODING_DIM = 32
input_embedding = tf.keras.layers.Input(shape=(embedding.shape[1],))
encoded = tf.keras.layers.Dense(128,activation='relu')(input_embedding)
encoded = tf.keras.layers.Dense(64,activation='relu')(encoded)
encoded = tf.keras.layers.Dense(ENCODING_DIM,activation='relu')(encoded)

decoded = tf.keras.layers.Dense(64, activation='relu')(encoded)
decoded = tf.keras.layers.Dense(128, activation='relu')(decoded)
decoded = tf.keras.layers.Dense(embedding.shape[1], activation='linear')(decoded)

autoencoder = tf.keras.models.Model(input_embedding, decoded)
autoencoder.compile(optimizer='adam', loss='mse')

In [17]:
autoencoder.fit(embedding, 
                embedding, 
                epochs=100, 
                batch_size=128, 
                shuffle=True)

Epoch 1/100
396/396 [==============================] - 4s 4ms/step - loss: 0.1087
Epoch 2/100
396/396 [==============================] - 2s 4ms/step - loss: 0.0824
Epoch 3/100
396/396 [==============================] - 2s 4ms/step - loss: 0.0781
Epoch 4/100
396/396 [==============================] - 2s 4ms/step - loss: 0.0768
Epoch 5/100
396/396 [==============================] - 2s 4ms/step - loss: 0.0760
Epoch 6/100
396/396 [==============================] - 2s 4ms/step - loss: 0.0752
Epoch 7/100
396/396 [==============================] - 2s 4ms/step - loss: 0.0746
Epoch 8/100
396/396 [==============================] - 2s 4ms/step - loss: 0.0739
Epoch 9/100
396/396 [==============================] - 2s 4ms/step - loss: 0.0733
Epoch 10/100
396/396 [==============================] - 2s 4ms/step - loss: 0.0727
Epoch 11/100
396/396 [==============================] - 2s 4ms/step - loss: 0.0722
Epoch 12/100
396/396 [==============================] - 2s 4ms/step - loss: 0.0718
Epoch 13/100


In [18]:
encoder = tf.keras.models.Model(input_embedding,encoded)
encoded_sentence_embeddings = encoder.predict(embedding)

## Visualization BERT with dimensional Reduction

In [19]:
tSNE = TSNE(n_components=2,init='pca',random_state=98)
embedding_matrix = tSNE.fit_transform(encoded_sentence_embeddings)

df_embedding = pd.DataFrame(embedding_matrix, columns=['X_TSNE','Y_TSNE'])
cluster_colors = {0: 'blue', 1: 'green', 2: 'yellow', 
                  3: 'red', 4: 'skyblue', 5:'salmon',
                 6:'black',7:'lightgreen',8:'purple'}
df_embedding['topic_idx'] =  cluster_assignment
df_embedding['color'] = df_embedding['topic_idx'].map(cluster_colors)
cluster_labels = {0: 'Mental Health During Pandemic', 1: 'Treatment Methods', 2: 'Drug Treatment Effect', 
                  3: 'Pandemic Impact On Daily Life', 4: 'Respiratory Condition On Infected Patient', 5:'School Activity During Pandemic',
                 6:'Transmission Dynamic Of Virus', 7: 'Mortality', 8:'Analysis and Technology'}
df_embedding['label'] = df_embedding['topic_idx'].map(cluster_labels)
df_embedding['article_title'] = list(data['title'])

output_notebook()

source = ColumnDataSource(
    dict(x = df_embedding['X_TSNE'],
         y = df_embedding['Y_TSNE'],
         color=df_embedding['color'],
         label=df_embedding['label'],
         topic_key= df_embedding['topic_idx'],
         title= df_embedding['article_title'],
        ))

lda_plot = figure(title='T-SNE Clustering of Documents: Embeddings after Dimension Reduction', 
              plot_width=800, plot_height=600,
              tools='pan,wheel_zoom,box_zoom,reset,hover', 
              x_axis_type=None, y_axis_type=None)
lda_plot.scatter(x='x', y='y', source=source, 
                 legend='label', color='color',alpha=0.7, size=10)
hover = lda_plot.select(dict(type=HoverTool))
hover.tooltips = {'content':'Title: @title'}
lda_plot.legend.location = 'bottom_right'
show(lda_plot)

- From the cluster above, we can see that there are a lot of overlapping between each topic, it seems like LDA performs better on gaining topic.